In [24]:
from keras.models import load_model
import time
import numpy as np
import heapq


# Data

In [27]:
file_name = input('TXT File Name: ')
text = open(file_name+'.txt', encoding="utf8").read()
print('corpus length:', len(text))

TXT File Name: todes
corpus length: 4293166


In [28]:
chars = sorted(list(set(text)))
char_indices = dict((c, i) for i, c in enumerate(chars))
indices_char = dict((i, c) for i, c in enumerate(chars))

print(f'unique chars: {len(chars)}')

SEQUENCE_LENGTH = 80
step = 4
sentences = []
next_chars = []
for i in range(0, len(text) - SEQUENCE_LENGTH, step):
    sentences.append(text[i: i + SEQUENCE_LENGTH])
    next_chars.append(text[i + SEQUENCE_LENGTH])
print(f'num training examples: {len(sentences)}')

X = np.zeros((len(sentences), SEQUENCE_LENGTH, len(chars)), dtype=np.bool)
y = np.zeros((len(sentences), len(chars)), dtype=np.bool)
for i, sentence in enumerate(sentences):
    for t, char in enumerate(sentence):
        X[i, t, char_indices[char]] = 1
    y[i, char_indices[next_chars[i]]] = 1

print("X.shape:", X.shape)
print("y.shape:", y.shape)

unique chars: 63
num training examples: 1073272
X.shape: (1073272, 80, 63)
y.shape: (1073272, 63)


# Functions

In [29]:
def prepare_input(text):
    x = np.zeros((1, SEQUENCE_LENGTH, len(chars)))
    for t, char in enumerate(text):
        x[0, t, char_indices[char]] = 1.
    return x

def temperatureSample(preds, temperature=1.0):
    preds = np.asarray(preds).astype('float64')
    preds = np.log(preds) / temperature
    exp_preds = np.exp(preds)
    preds = exp_preds / np.sum(exp_preds)
    probas = np.random.multinomial(1, preds, 1)
    return np.argmax(probas)

def sample(preds, top_n=3):
    preds = np.asarray(preds).astype('float64')
    preds = np.log(preds)
    exp_preds = np.exp(preds)
    preds = exp_preds / np.sum(exp_preds)

    return heapq.nlargest(top_n, range(len(preds)), preds.take)

def predict_completion(text):
    original_text = text
    generated = text
    completion = ''
    while True:
        x = prepare_input(text)
        preds = model.predict(x, verbose=0)[0]
        next_index = sample(preds, top_n=1)[0]
        next_char = indices_char[next_index]
        text = text[1:] + next_char
        completion += next_char
        if len(original_text + completion) + 2 > len(original_text) and next_char == ' ':
            return completion

def predict_completions(text, n=3): 
    x = prepare_input(text)
    preds = model.predict(x, verbose=0)[0]
    next_indices = sample(preds, n)
    return [indices_char[idx] + predict_completion(text[1:] + indices_char[idx]) for idx in next_indices]



timestr = time.strftime("%Y%m%d-%H%M%S")

# Load model and predict

In [39]:
model = load_model('models/todes_model.h5')

In [49]:
SEQUENCE_LENGTH = 80
MAX_TWITTER_CHARS = 280

In [53]:
def genSentence(text, words = 2):
    textOG = text
    text = text.lower()
    while len(text) < SEQUENCE_LENGTH:
        text = ' ' + text
    text = text[-SEQUENCE_LENGTH:]
    for i in range(words):
        text = text[-SEQUENCE_LENGTH:]
        pred = predict_completions(text, 1)[0]
        text = text + pred
        textOG = textOG + pred
        #print(text)
        pass
    return textOG

def getTweet(text, tweet_length):
    test_txt = genSentence(text, 1)

    while len(test_txt)<=MAX_TWITTER_CHARS:
        test_txt = genSentence(test_txt, 1)
    return test_txt


In [55]:
getTweet("cuando",MAX_TWITTER_CHARS)

'cuando se vuelve vi con al se que es la protega lo que no se tuvo a todes hace un pasado para todes les que hacen las personas entiendo el lenguaje natural y critican que a alguien le d su gana decir deli, lo ms conocer a todes les que hacen las personas entiendo el lenguaje natural '

------

# Fun results

**entonces** te acuesta a la oportunidad y carajo en la presentacin del autocultivo en santa fe. por una planta que sea de y para todes. #marihuanaparalasalud #encuarentena #cannabisesencial

    construyendo una patria con todes y para todes la media sancin de la regulacin del autocultivo en santa fe. por una planta que sea de y para todes. #marihuanaparalasalud #encuarentena #cannabisesencial

In [47]:
text

'la cuarentena nos afecta a todespusimos en marcha el #plannacional2020 junto al presidente de la nacin @alferdez, un paso fundamental hacia una sociedad ms justa, igualitaria y libre de violencias para todas, todes y todos. identificados ya? #elmacrismoesviolencia decididxs a construir futuro a travs de un proyecto que haga de bs as una ciudad habitable en la que todos, todas y todes tengan acceso a la salud y a la vivienda. una metrpolis innovadora que se referencie en la regin como la ciudad del conocimiento. #gb #casacomn las imgenes de la manifestacin de hoy y no puedo dejar de pensar en el incumplimiento del aislamiento social, preventivo y obligatorio. cuidarnos a cada uno/a entre todas, todos y todes es responsabilidad institucional para el gobierno, pero tambin para la oposicin.qudate tranquilo @feriglesias nuestro gobierno lleg para cuidar a todes, incluidos los pelotudos mala leche como vos identificados ya? #elmacrismoesviolencia tambien soy!!! pero todes me atacan por mama